In [1]:
import numpy as np

In [2]:
# 将当前变量空间中的数据映射到高维空间中，使用更高维度的超平面划分数据
# 相当于在高维空间解决线性问题，相当于在低维空间解决非线性问题

In [3]:
# 将数据扁平化
def img2vector(filename):
    fr = open(filename)
    lines = fr.readlines()
    returnVect = np.array([list(line.strip()) for line in lines],dtype=np.int32).flatten()
    return returnVect
def img2vector1(filename):
    returnVect = np.zeros((1,1024))
    fr = open(filename)
    for i in range(32):
        lineStr = fr.readline()
        for j in range(32):
            returnVect[0,32*i+j] = int(lineStr[j])
    return returnVect

In [4]:
# 加载多个手写字数据文件
#二分类问题
def loadImages(dirName):
    from os import listdir
    hwlabels = []
    trainingFileList = listdir(dirName)
    m = len(trainingFileList)
    trainingMat = np.zeros((m,1024))
    print('%d 条数据'%m)
    for i in range(m):
        fileNameStr = trainingFileList[i]
        classNum = int(fileNameStr.split('.')[0].split('_')[0])
        if classNum == 9:
            hwlabels.append(-1)
        else:
            hwlabels.append(1)
        trainingMat[i,:] = img2vector1("%s/%s"%(dirName,fileNameStr))
    return trainingMat,hwlabels

# 多分类问题
def loadImages1(dirName):
    from os import listdir
    hwlabels = []
    trainingFileList = listdir(dirName)
    m = len(trainingFileList)
#     print('%d 条数据'%m)
    trainingMat = np.zeros((m,1024))
    for i in range(m):
        fileNameStr = trainingFileList[i]
        classNum = int(fileNameStr.split('.')[0].split('_')[0])
        hwlabels.append(classNum)
        trainingMat[i,:] = img2vector1("%s/%s"%(dirName,fileNameStr))
#     print(hwlabels)
    hwlabelMat10Class = np.mat(np.zeros((10,m))) # 横为类别，竖为编号
    hwlabelMat = np.mat(hwlabels)
    for i in range(10):
        mat = hwlabelMat.copy()
        mat[mat != i] = -1
        mat[mat == i] = 1
        hwlabelMat10Class[i,:] = mat
    return trainingMat,hwlabelMat10Class

In [5]:
# 全局数据存贮对象
class optStruct:
    def __init__(self,dataMatIn,classLabels,C,toler,kTup):
        self.X = dataMatIn
        self.labelMat = classLabels
        self.C = C
        self.tol = toler
        self.m = np.shape(dataMatIn)[0]
        self.alphas = np.mat(np.zeros((self.m,1)))
        self.b = 0
        self.eCache = np.mat(np.zeros((self.m,2))) # [1,Ek] 第一位是使能标志位，第二位是Ek值
        self.K = np.mat(np.zeros((self.m,self.m))) 
        for i in range(self.m):
            self.K[:,i] = kernelTrans(self.X,self.X[i,:],kTup)

In [6]:
# 核函数
# 一列代表一个向量与输入矩阵內积计算值列表
def kernelTrans(X,A,kTup):
    m,n = np.shape(X)
    K = np.mat(np.zeros((m,1)))
    if kTup[0] == "lin":K =X *A.T
    elif kTup[0] == "rbf":
        for j in range(m):
            deltaRow =X[j,:] - A
            K[j] = deltaRow * deltaRow.T
        K = np.exp(K/(-2*kTup[1]**2))
    else: raise NameError('核函数出错')
    return K

In [7]:
# 计算误差值
def calcEk(oS,k):
    fXk = float(np.multiply(oS.alphas,oS.labelMat).T*oS.K[:,k] + oS.b)
    Ek = fXk - float(oS.labelMat[k])
    return Ek

In [8]:
# 从剩余alpha索引中随机选择一个
# i aplha下标
# m 所有alpha的数目
def selectJrand(i,m):
    j = i 
    while(j == i): # 保证从剩余中选取
        j = int(np.random.uniform(1,m))
    return j

In [9]:
# 启发式选取内层循环的j索引
def selectJ(i,oS,Ei):
    maxK = -1
    maxDeltaE = 0
    Ej = 0
    oS.eCache[i] = [1,Ei]
    validEcacheList = np.nonzero(oS.eCache[:,0].A)[0] # 已计算过E值的j索引
    if len(validEcacheList) > 1:
        for k in validEcacheList:
            if k == i :
                continue
            Ek = calcEk(oS,k) # 重新计算
            deltaE = abs(Ei-Ek) # 选取E最大值对应的j
            if deltaE > maxDeltaE:
                maxK = k
                maxDeltaE = deltaE
                Ej = Ek
        return maxK,Ej
    else:
        j = selectJrand(i,oS.m) # 第一次寻找，随机寻找
        Ej = calcEk(oS,j)
    return j,Ej

In [10]:
#  调整大于H或小于L的aplha值
def clipAlpha(aj,H,L):
    if aj > H:
        aj = H
    elif aj < L:
        aj = L
    return aj

In [11]:
# alpha值优化后需要存储Ek
def updateEk(oS,k):
    Ek = calcEk(oS,k)
    oS.eCache[k] = [1,Ek]

In [12]:
def innerL(i,oS):
    Ei = calcEk(oS,i)
    # 测试容错率
    if ((oS.labelMat[i]*Ei < -oS.tol) and (oS.alphas[i] <oS.C)) or ((oS.labelMat[i]*Ei > oS.tol)and(oS.alphas[i] >0)):
        j,Ej = selectJ(i,oS,Ei)
        alphaIold = oS.alphas[i].copy()
        alphaJold = oS.alphas[j].copy()
        if (oS.labelMat[i] != oS.labelMat[j]):
            L = max(0,oS.alphas[j] - oS.alphas[i])
            H = min(oS.C,oS.C + oS.alphas[j] - oS.alphas[i])
        else:
            L = max(0,oS.alphas[j] + oS.alphas[i] -oS.C)
            H = min(oS.C,oS.alphas[j] + oS.alphas[i])
        if L==H:print("L==H");return 0
        eta = 2.0 * oS.K[i,j] - oS.K[i,i] - oS.K[j,j] # 核函数
        if eta >=0: print('eta >= 0 ');return 0
        oS.alphas[j] -= oS.labelMat[j]*(Ei - Ej)/eta
        oS.alphas[j] = clipAlpha(oS.alphas[j],H,L)
        updateEk(oS,j)
        if abs(oS.alphas[j] - alphaJold) < 0.00001:
            print('j not moving enough')
            return 0
        oS.alphas[i] += oS.labelMat[j]*oS.labelMat[i]*(alphaJold - oS.alphas[j])
        updateEk(oS,i)
        b1 = oS.b - Ei - oS.labelMat[i]*(oS.alphas[i]-alphaIold)*oS.K[i,i]  - oS.labelMat[j]*(oS.alphas[j]-alphaJold)*oS.K[i,j]
        b2 = oS.b - Ej - oS.labelMat[i]*(oS.alphas[i]-alphaIold)*oS.K[i,i]  - oS.labelMat[j]*(oS.alphas[j]-alphaJold)*oS.K[i,j]
        if  (0<oS.alphas[i]) and (oS.C > oS.alphas[i]):
            oS.b = b1
        elif (0<oS.alphas[j]) and (oS.C > oS.alphas[j]):
            oS.b = b2
        else:
            oS.b = (b1+b2)/2.0
        return 1
    else:
        return 0

In [13]:
def smoP(dataMatIn,classLabels,C,toler,maxIter,kTup):
    oS = optStruct(np.mat(dataMatIn),np.mat(classLabels).transpose(),C,toler,kTup)
    iterNum = 0
    entireSet = True
    alphaPairsChanged = 0
    while(iterNum<maxIter) and ((alphaPairsChanged >0)or entireSet):
        alphaPairsChanged = 0
        if entireSet:
            for i in range(oS.m):
                alphaPairsChanged += innerL(i,oS)
                print('fullset, iterNUm: %d i: %d, pairs changed %d'%(iterNum,i,alphaPairsChanged))
            iterNum += 1
        else:
            nonBoundIs = np.nonzero((oS.alphas.A >0)*(oS.alphas.A<C))[0]
            for i in nonBoundIs:
                alphaPairsChanged += innerL(i,oS)
                print("non-bound, iterNum:%d i:%d, pairs changed %d"%(iterNum,i,alphaPairsChanged))
            iterNum += 1
        if entireSet:
            entireSet = False
        elif alphaPairsChanged == 0:
            entireSet = True
        print('iteration number: %d'%iterNum)
    return oS.b,oS.alphas

In [14]:
def testDigits(trainData,testData,kTup=('rbf',10)):
#     dataArr,labelArr = loadImages('./digits/trainingDigits/')
    dataArr = trainData[0]
    labelArr = trainData[1]
    b,alphas = smoP(dataArr,labelArr,200,0.0001,10000,kTup)
    dataMat = np.mat(dataArr)
    labelMat = np.mat(labelArr).transpose()
    svInd = np.nonzero(alphas.A>0)[0]
    sVs = dataMat[svInd]
    labelSV = labelMat[svInd]
    print('支持向量数: %d'%np.shape(sVs)[0])
    m,n = np.shape(dataMat)
    errorCount = 0
#     weights = dataMat.T*np.multiply(alphas,labelMat)
#     dataMat[0]*weights+b
    for i in range(m):
        kernelEval = kernelTrans(sVs,dataMat[i,:],kTup) # 挑出alphas非零的数据，因为其他数据即使做了核变换最后也会变成0
        predict = kernelEval.T * np.multiply(labelSV,alphas[svInd])+b
        if np.sign(predict) != np.sign(labelArr[i]):errorCount += 1
#         print("%f,%f"%(np.sign(predict),np.sign(labelArr[i])))        
    print('训练集错误率为:%f'%(errorCount/m))
#     dataArr2,labelArr2 = loadImages('./digits/testDigits/')
    dataArr2 = testData[0]
    labelArr2 =testData[1]
    dataMat2 = np.mat(dataArr2)
    labelMat2 = np.mat(labelArr2).transpose()
    m2,n2 = np.shape(dataMat2)
    errorCount2 = 0
    for i in range(m2):
        kernelEval = kernelTrans(sVs,dataMat2[i,:],kTup) # 挑出alphas非零的数据，因为其他数据即使做了核变换最后也会变成0,s所以只需要和支持向量乘就可以了
        predict = kernelEval.T * np.multiply(labelSV,alphas[svInd])+b
        if np.sign(predict) != np.sign(labelArr2[i]):
            errorCount2 += 1
#         print("%f,%f"%(np.sign(predict),np.sign(labelArr2[i])))
    print('测试集错误率为:%f'%(errorCount2/m2))

In [15]:
trainData = loadImages('./digits/trainingDigits/')
testData = loadImages('./digits/testDigits/')

1934 条数据
946 条数据


In [16]:
testDigits(trainData,testData,('rbf',0.1))

L==H
fullset, iterNUm: 0 i: 0, pairs changed 0
fullset, iterNUm: 0 i: 1, pairs changed 1
fullset, iterNUm: 0 i: 2, pairs changed 2
fullset, iterNUm: 0 i: 3, pairs changed 3
fullset, iterNUm: 0 i: 4, pairs changed 4
fullset, iterNUm: 0 i: 5, pairs changed 5
fullset, iterNUm: 0 i: 6, pairs changed 6
fullset, iterNUm: 0 i: 7, pairs changed 7
fullset, iterNUm: 0 i: 8, pairs changed 8
fullset, iterNUm: 0 i: 9, pairs changed 9
fullset, iterNUm: 0 i: 10, pairs changed 10
fullset, iterNUm: 0 i: 11, pairs changed 11
fullset, iterNUm: 0 i: 12, pairs changed 12
fullset, iterNUm: 0 i: 13, pairs changed 13
fullset, iterNUm: 0 i: 14, pairs changed 14
fullset, iterNUm: 0 i: 15, pairs changed 15
fullset, iterNUm: 0 i: 16, pairs changed 16
fullset, iterNUm: 0 i: 17, pairs changed 17
fullset, iterNUm: 0 i: 18, pairs changed 18
fullset, iterNUm: 0 i: 19, pairs changed 19
fullset, iterNUm: 0 i: 20, pairs changed 20
fullset, iterNUm: 0 i: 21, pairs changed 21
fullset, iterNUm: 0 i: 22, pairs changed 22
ful

fullset, iterNUm: 0 i: 193, pairs changed 193
fullset, iterNUm: 0 i: 194, pairs changed 194
fullset, iterNUm: 0 i: 195, pairs changed 195
fullset, iterNUm: 0 i: 196, pairs changed 196
fullset, iterNUm: 0 i: 197, pairs changed 197
fullset, iterNUm: 0 i: 198, pairs changed 198
fullset, iterNUm: 0 i: 199, pairs changed 199
fullset, iterNUm: 0 i: 200, pairs changed 200
fullset, iterNUm: 0 i: 201, pairs changed 201
fullset, iterNUm: 0 i: 202, pairs changed 202
fullset, iterNUm: 0 i: 203, pairs changed 203
fullset, iterNUm: 0 i: 204, pairs changed 204
fullset, iterNUm: 0 i: 205, pairs changed 205
fullset, iterNUm: 0 i: 206, pairs changed 206
fullset, iterNUm: 0 i: 207, pairs changed 207
fullset, iterNUm: 0 i: 208, pairs changed 208
fullset, iterNUm: 0 i: 209, pairs changed 209
fullset, iterNUm: 0 i: 210, pairs changed 210
fullset, iterNUm: 0 i: 211, pairs changed 211
fullset, iterNUm: 0 i: 212, pairs changed 212
fullset, iterNUm: 0 i: 213, pairs changed 213
fullset, iterNUm: 0 i: 214, pairs 

fullset, iterNUm: 0 i: 385, pairs changed 385
fullset, iterNUm: 0 i: 386, pairs changed 386
fullset, iterNUm: 0 i: 387, pairs changed 387
fullset, iterNUm: 0 i: 388, pairs changed 388
fullset, iterNUm: 0 i: 389, pairs changed 389
fullset, iterNUm: 0 i: 390, pairs changed 390
fullset, iterNUm: 0 i: 391, pairs changed 391
fullset, iterNUm: 0 i: 392, pairs changed 392
fullset, iterNUm: 0 i: 393, pairs changed 393
fullset, iterNUm: 0 i: 394, pairs changed 394
fullset, iterNUm: 0 i: 395, pairs changed 395
fullset, iterNUm: 0 i: 396, pairs changed 396
fullset, iterNUm: 0 i: 397, pairs changed 397
fullset, iterNUm: 0 i: 398, pairs changed 398
fullset, iterNUm: 0 i: 399, pairs changed 399
fullset, iterNUm: 0 i: 400, pairs changed 400
fullset, iterNUm: 0 i: 401, pairs changed 401
fullset, iterNUm: 0 i: 402, pairs changed 402
fullset, iterNUm: 0 i: 403, pairs changed 403
fullset, iterNUm: 0 i: 404, pairs changed 404
fullset, iterNUm: 0 i: 405, pairs changed 405
fullset, iterNUm: 0 i: 406, pairs 

fullset, iterNUm: 0 i: 572, pairs changed 572
fullset, iterNUm: 0 i: 573, pairs changed 573
fullset, iterNUm: 0 i: 574, pairs changed 574
fullset, iterNUm: 0 i: 575, pairs changed 575
fullset, iterNUm: 0 i: 576, pairs changed 576
fullset, iterNUm: 0 i: 577, pairs changed 577
fullset, iterNUm: 0 i: 578, pairs changed 578
fullset, iterNUm: 0 i: 579, pairs changed 579
fullset, iterNUm: 0 i: 580, pairs changed 580
fullset, iterNUm: 0 i: 581, pairs changed 581
fullset, iterNUm: 0 i: 582, pairs changed 582
fullset, iterNUm: 0 i: 583, pairs changed 583
fullset, iterNUm: 0 i: 584, pairs changed 584
fullset, iterNUm: 0 i: 585, pairs changed 585
fullset, iterNUm: 0 i: 586, pairs changed 586
fullset, iterNUm: 0 i: 587, pairs changed 587
fullset, iterNUm: 0 i: 588, pairs changed 588
fullset, iterNUm: 0 i: 589, pairs changed 589
fullset, iterNUm: 0 i: 590, pairs changed 590
fullset, iterNUm: 0 i: 591, pairs changed 591
fullset, iterNUm: 0 i: 592, pairs changed 592
fullset, iterNUm: 0 i: 593, pairs 

fullset, iterNUm: 0 i: 753, pairs changed 753
fullset, iterNUm: 0 i: 754, pairs changed 754
fullset, iterNUm: 0 i: 755, pairs changed 755
fullset, iterNUm: 0 i: 756, pairs changed 756
fullset, iterNUm: 0 i: 757, pairs changed 757
fullset, iterNUm: 0 i: 758, pairs changed 758
fullset, iterNUm: 0 i: 759, pairs changed 759
fullset, iterNUm: 0 i: 760, pairs changed 760
fullset, iterNUm: 0 i: 761, pairs changed 761
fullset, iterNUm: 0 i: 762, pairs changed 762
fullset, iterNUm: 0 i: 763, pairs changed 763
fullset, iterNUm: 0 i: 764, pairs changed 764
fullset, iterNUm: 0 i: 765, pairs changed 765
fullset, iterNUm: 0 i: 766, pairs changed 766
fullset, iterNUm: 0 i: 767, pairs changed 767
fullset, iterNUm: 0 i: 768, pairs changed 768
fullset, iterNUm: 0 i: 769, pairs changed 769
fullset, iterNUm: 0 i: 770, pairs changed 770
fullset, iterNUm: 0 i: 771, pairs changed 771
fullset, iterNUm: 0 i: 772, pairs changed 772
fullset, iterNUm: 0 i: 773, pairs changed 773
fullset, iterNUm: 0 i: 774, pairs 

...

non-bound, iterNum:4 i:1748, pairs changed 1422
non-bound, iterNum:4 i:1749, pairs changed 1423
non-bound, iterNum:4 i:1750, pairs changed 1424
non-bound, iterNum:4 i:1751, pairs changed 1425
non-bound, iterNum:4 i:1752, pairs changed 1426
non-bound, iterNum:4 i:1753, pairs changed 1427
non-bound, iterNum:4 i:1754, pairs changed 1428
non-bound, iterNum:4 i:1755, pairs changed 1429
non-bound, iterNum:4 i:1756, pairs changed 1430
non-bound, iterNum:4 i:1757, pairs changed 1431
non-bound, iterNum:4 i:1758, pairs changed 1432
non-bound, iterNum:4 i:1759, pairs changed 1433
non-bound, iterNum:4 i:1760, pairs changed 1434
non-bound, iterNum:4 i:1761, pairs changed 1435
non-bound, iterNum:4 i:1762, pairs changed 1436
non-bound, iterNum:4 i:1763, pairs changed 1437
non-bound, iterNum:4 i:1764, pairs changed 1438
non-bound, iterNum:4 i:1765, pairs changed 1439
non-bound, iterNum:4 i:1766, pairs changed 1440
non-bound, iterNum:4 i:1767, pairs changed 1441
non-bound, iterNum:4 i:1768, pairs chang

non-bound, iterNum:4 i:1921, pairs changed 1542
non-bound, iterNum:4 i:1922, pairs changed 1543
non-bound, iterNum:4 i:1923, pairs changed 1544
non-bound, iterNum:4 i:1924, pairs changed 1545
non-bound, iterNum:4 i:1925, pairs changed 1546
non-bound, iterNum:4 i:1926, pairs changed 1547
non-bound, iterNum:4 i:1927, pairs changed 1547
non-bound, iterNum:4 i:1928, pairs changed 1547
non-bound, iterNum:4 i:1929, pairs changed 1547
non-bound, iterNum:4 i:1930, pairs changed 1547
non-bound, iterNum:4 i:1931, pairs changed 1547
non-bound, iterNum:4 i:1932, pairs changed 1547
non-bound, iterNum:4 i:1933, pairs changed 1547
iteration number: 5
non-bound, iterNum:5 i:0, pairs changed 0
non-bound, iterNum:5 i:1, pairs changed 0
non-bound, iterNum:5 i:2, pairs changed 0
non-bound, iterNum:5 i:3, pairs changed 0
non-bound, iterNum:5 i:4, pairs changed 0
non-bound, iterNum:5 i:5, pairs changed 0
non-bound, iterNum:5 i:6, pairs changed 0
non-bound, iterNum:5 i:7, pairs changed 0
non-bound, iterNum:5

non-bound, iterNum:5 i:969, pairs changed 0
non-bound, iterNum:5 i:970, pairs changed 0
non-bound, iterNum:5 i:971, pairs changed 0
non-bound, iterNum:5 i:972, pairs changed 0
non-bound, iterNum:5 i:973, pairs changed 0
non-bound, iterNum:5 i:974, pairs changed 0
non-bound, iterNum:5 i:975, pairs changed 0
non-bound, iterNum:5 i:976, pairs changed 0
non-bound, iterNum:5 i:977, pairs changed 0
non-bound, iterNum:5 i:978, pairs changed 0
non-bound, iterNum:5 i:979, pairs changed 0
non-bound, iterNum:5 i:980, pairs changed 0
non-bound, iterNum:5 i:981, pairs changed 0
non-bound, iterNum:5 i:982, pairs changed 0
non-bound, iterNum:5 i:983, pairs changed 0
non-bound, iterNum:5 i:984, pairs changed 0
non-bound, iterNum:5 i:985, pairs changed 0
non-bound, iterNum:5 i:986, pairs changed 0
non-bound, iterNum:5 i:987, pairs changed 0
non-bound, iterNum:5 i:988, pairs changed 0
non-bound, iterNum:5 i:989, pairs changed 0
non-bound, iterNum:5 i:990, pairs changed 0
non-bound, iterNum:5 i:991, pair

fullset, iterNUm: 6 i: 1526, pairs changed 0
fullset, iterNUm: 6 i: 1527, pairs changed 0
fullset, iterNUm: 6 i: 1528, pairs changed 0
fullset, iterNUm: 6 i: 1529, pairs changed 0
fullset, iterNUm: 6 i: 1530, pairs changed 0
fullset, iterNUm: 6 i: 1531, pairs changed 0
fullset, iterNUm: 6 i: 1532, pairs changed 0
fullset, iterNUm: 6 i: 1533, pairs changed 0
fullset, iterNUm: 6 i: 1534, pairs changed 0
fullset, iterNUm: 6 i: 1535, pairs changed 0
fullset, iterNUm: 6 i: 1536, pairs changed 0
fullset, iterNUm: 6 i: 1537, pairs changed 0
fullset, iterNUm: 6 i: 1538, pairs changed 0
fullset, iterNUm: 6 i: 1539, pairs changed 0
fullset, iterNUm: 6 i: 1540, pairs changed 0
fullset, iterNUm: 6 i: 1541, pairs changed 0
fullset, iterNUm: 6 i: 1542, pairs changed 0
fullset, iterNUm: 6 i: 1543, pairs changed 0
fullset, iterNUm: 6 i: 1544, pairs changed 0
fullset, iterNUm: 6 i: 1545, pairs changed 0
fullset, iterNUm: 6 i: 1546, pairs changed 0
fullset, iterNUm: 6 i: 1547, pairs changed 0
fullset, i

测试集错误率为:0.094080


In [20]:
testDigits(trainData,testData,('rbf',1))

L==H
fullset, iterNUm: 0 i: 0, pairs changed 0
fullset, iterNUm: 0 i: 1, pairs changed 1
fullset, iterNUm: 0 i: 2, pairs changed 2
fullset, iterNUm: 0 i: 3, pairs changed 3
fullset, iterNUm: 0 i: 4, pairs changed 4
fullset, iterNUm: 0 i: 5, pairs changed 5
fullset, iterNUm: 0 i: 6, pairs changed 6
fullset, iterNUm: 0 i: 7, pairs changed 7
fullset, iterNUm: 0 i: 8, pairs changed 8
fullset, iterNUm: 0 i: 9, pairs changed 9
fullset, iterNUm: 0 i: 10, pairs changed 10
fullset, iterNUm: 0 i: 11, pairs changed 11
fullset, iterNUm: 0 i: 12, pairs changed 12
fullset, iterNUm: 0 i: 13, pairs changed 13
fullset, iterNUm: 0 i: 14, pairs changed 14
fullset, iterNUm: 0 i: 15, pairs changed 15
fullset, iterNUm: 0 i: 16, pairs changed 16
fullset, iterNUm: 0 i: 17, pairs changed 17
fullset, iterNUm: 0 i: 18, pairs changed 18
fullset, iterNUm: 0 i: 19, pairs changed 19
fullset, iterNUm: 0 i: 20, pairs changed 20
fullset, iterNUm: 0 i: 21, pairs changed 21
fullset, iterNUm: 0 i: 22, pairs changed 22
ful

fullset, iterNUm: 0 i: 195, pairs changed 195
fullset, iterNUm: 0 i: 196, pairs changed 196
fullset, iterNUm: 0 i: 197, pairs changed 197
fullset, iterNUm: 0 i: 198, pairs changed 198
fullset, iterNUm: 0 i: 199, pairs changed 199
fullset, iterNUm: 0 i: 200, pairs changed 200
fullset, iterNUm: 0 i: 201, pairs changed 201
fullset, iterNUm: 0 i: 202, pairs changed 202
fullset, iterNUm: 0 i: 203, pairs changed 203
fullset, iterNUm: 0 i: 204, pairs changed 204
fullset, iterNUm: 0 i: 205, pairs changed 205
fullset, iterNUm: 0 i: 206, pairs changed 206
fullset, iterNUm: 0 i: 207, pairs changed 207
fullset, iterNUm: 0 i: 208, pairs changed 208
fullset, iterNUm: 0 i: 209, pairs changed 209
fullset, iterNUm: 0 i: 210, pairs changed 210
fullset, iterNUm: 0 i: 211, pairs changed 211
fullset, iterNUm: 0 i: 212, pairs changed 212
fullset, iterNUm: 0 i: 213, pairs changed 213
fullset, iterNUm: 0 i: 214, pairs changed 214
fullset, iterNUm: 0 i: 215, pairs changed 215
fullset, iterNUm: 0 i: 216, pairs 

fullset, iterNUm: 0 i: 386, pairs changed 386
fullset, iterNUm: 0 i: 387, pairs changed 387
fullset, iterNUm: 0 i: 388, pairs changed 388
fullset, iterNUm: 0 i: 389, pairs changed 389
fullset, iterNUm: 0 i: 390, pairs changed 390
fullset, iterNUm: 0 i: 391, pairs changed 391
fullset, iterNUm: 0 i: 392, pairs changed 392
fullset, iterNUm: 0 i: 393, pairs changed 393
fullset, iterNUm: 0 i: 394, pairs changed 394
fullset, iterNUm: 0 i: 395, pairs changed 395
fullset, iterNUm: 0 i: 396, pairs changed 396
fullset, iterNUm: 0 i: 397, pairs changed 397
fullset, iterNUm: 0 i: 398, pairs changed 398
fullset, iterNUm: 0 i: 399, pairs changed 399
fullset, iterNUm: 0 i: 400, pairs changed 400
fullset, iterNUm: 0 i: 401, pairs changed 401
fullset, iterNUm: 0 i: 402, pairs changed 402
fullset, iterNUm: 0 i: 403, pairs changed 403
fullset, iterNUm: 0 i: 404, pairs changed 404
fullset, iterNUm: 0 i: 405, pairs changed 405
fullset, iterNUm: 0 i: 406, pairs changed 406
fullset, iterNUm: 0 i: 407, pairs 

fullset, iterNUm: 0 i: 572, pairs changed 572
fullset, iterNUm: 0 i: 573, pairs changed 573
fullset, iterNUm: 0 i: 574, pairs changed 574
fullset, iterNUm: 0 i: 575, pairs changed 575
fullset, iterNUm: 0 i: 576, pairs changed 576
fullset, iterNUm: 0 i: 577, pairs changed 577
fullset, iterNUm: 0 i: 578, pairs changed 578
fullset, iterNUm: 0 i: 579, pairs changed 579
fullset, iterNUm: 0 i: 580, pairs changed 580
fullset, iterNUm: 0 i: 581, pairs changed 581
fullset, iterNUm: 0 i: 582, pairs changed 582
fullset, iterNUm: 0 i: 583, pairs changed 583
fullset, iterNUm: 0 i: 584, pairs changed 584
fullset, iterNUm: 0 i: 585, pairs changed 585
fullset, iterNUm: 0 i: 586, pairs changed 586
fullset, iterNUm: 0 i: 587, pairs changed 587
fullset, iterNUm: 0 i: 588, pairs changed 588
fullset, iterNUm: 0 i: 589, pairs changed 589
fullset, iterNUm: 0 i: 590, pairs changed 590
fullset, iterNUm: 0 i: 591, pairs changed 591
fullset, iterNUm: 0 i: 592, pairs changed 592
fullset, iterNUm: 0 i: 593, pairs 

fullset, iterNUm: 0 i: 755, pairs changed 755
fullset, iterNUm: 0 i: 756, pairs changed 756
fullset, iterNUm: 0 i: 757, pairs changed 757
fullset, iterNUm: 0 i: 758, pairs changed 758
fullset, iterNUm: 0 i: 759, pairs changed 759
fullset, iterNUm: 0 i: 760, pairs changed 760
fullset, iterNUm: 0 i: 761, pairs changed 761
fullset, iterNUm: 0 i: 762, pairs changed 762
fullset, iterNUm: 0 i: 763, pairs changed 763
fullset, iterNUm: 0 i: 764, pairs changed 764
fullset, iterNUm: 0 i: 765, pairs changed 765
fullset, iterNUm: 0 i: 766, pairs changed 766
fullset, iterNUm: 0 i: 767, pairs changed 767
fullset, iterNUm: 0 i: 768, pairs changed 768
fullset, iterNUm: 0 i: 769, pairs changed 769
fullset, iterNUm: 0 i: 770, pairs changed 770
fullset, iterNUm: 0 i: 771, pairs changed 771
fullset, iterNUm: 0 i: 772, pairs changed 772
fullset, iterNUm: 0 i: 773, pairs changed 773
fullset, iterNUm: 0 i: 774, pairs changed 774
fullset, iterNUm: 0 i: 775, pairs changed 775
fullset, iterNUm: 0 i: 776, pairs 

...

non-bound, iterNum:5 i:1521, pairs changed 225
non-bound, iterNum:5 i:1522, pairs changed 225
non-bound, iterNum:5 i:1523, pairs changed 225
non-bound, iterNum:5 i:1524, pairs changed 225
non-bound, iterNum:5 i:1525, pairs changed 225
non-bound, iterNum:5 i:1526, pairs changed 225
non-bound, iterNum:5 i:1527, pairs changed 225
non-bound, iterNum:5 i:1528, pairs changed 225
non-bound, iterNum:5 i:1529, pairs changed 225
non-bound, iterNum:5 i:1530, pairs changed 226
non-bound, iterNum:5 i:1531, pairs changed 226
non-bound, iterNum:5 i:1532, pairs changed 226
non-bound, iterNum:5 i:1533, pairs changed 226
non-bound, iterNum:5 i:1534, pairs changed 226
non-bound, iterNum:5 i:1535, pairs changed 226
non-bound, iterNum:5 i:1536, pairs changed 226
non-bound, iterNum:5 i:1537, pairs changed 226
non-bound, iterNum:5 i:1538, pairs changed 226
non-bound, iterNum:5 i:1539, pairs changed 226
non-bound, iterNum:5 i:1540, pairs changed 226
non-bound, iterNum:5 i:1541, pairs changed 226
non-bound, it

non-bound, iterNum:5 i:1899, pairs changed 232
non-bound, iterNum:5 i:1900, pairs changed 232
non-bound, iterNum:5 i:1901, pairs changed 232
non-bound, iterNum:5 i:1902, pairs changed 232
non-bound, iterNum:5 i:1903, pairs changed 232
non-bound, iterNum:5 i:1904, pairs changed 232
non-bound, iterNum:5 i:1905, pairs changed 232
non-bound, iterNum:5 i:1906, pairs changed 232
non-bound, iterNum:5 i:1907, pairs changed 232
non-bound, iterNum:5 i:1908, pairs changed 232
non-bound, iterNum:5 i:1909, pairs changed 232
non-bound, iterNum:5 i:1910, pairs changed 232
non-bound, iterNum:5 i:1911, pairs changed 232
non-bound, iterNum:5 i:1912, pairs changed 232
non-bound, iterNum:5 i:1913, pairs changed 232
non-bound, iterNum:5 i:1914, pairs changed 232
non-bound, iterNum:5 i:1915, pairs changed 232
non-bound, iterNum:5 i:1916, pairs changed 232
non-bound, iterNum:5 i:1917, pairs changed 232
non-bound, iterNum:5 i:1918, pairs changed 232
non-bound, iterNum:5 i:1919, pairs changed 232
non-bound, it

fullset, iterNUm: 7 i: 196, pairs changed 0
fullset, iterNUm: 7 i: 197, pairs changed 0
fullset, iterNUm: 7 i: 198, pairs changed 0
fullset, iterNUm: 7 i: 199, pairs changed 0
fullset, iterNUm: 7 i: 200, pairs changed 0
fullset, iterNUm: 7 i: 201, pairs changed 0
fullset, iterNUm: 7 i: 202, pairs changed 0
fullset, iterNUm: 7 i: 203, pairs changed 0
fullset, iterNUm: 7 i: 204, pairs changed 0
fullset, iterNUm: 7 i: 205, pairs changed 0
fullset, iterNUm: 7 i: 206, pairs changed 0
fullset, iterNUm: 7 i: 207, pairs changed 0
fullset, iterNUm: 7 i: 208, pairs changed 0
fullset, iterNUm: 7 i: 209, pairs changed 0
fullset, iterNUm: 7 i: 210, pairs changed 0
fullset, iterNUm: 7 i: 211, pairs changed 0
fullset, iterNUm: 7 i: 212, pairs changed 0
fullset, iterNUm: 7 i: 213, pairs changed 0
fullset, iterNUm: 7 i: 214, pairs changed 0
fullset, iterNUm: 7 i: 215, pairs changed 0
fullset, iterNUm: 7 i: 216, pairs changed 0
fullset, iterNUm: 7 i: 217, pairs changed 0
fullset, iterNUm: 7 i: 218, pair

fullset, iterNUm: 7 i: 1484, pairs changed 0
fullset, iterNUm: 7 i: 1485, pairs changed 0
fullset, iterNUm: 7 i: 1486, pairs changed 0
fullset, iterNUm: 7 i: 1487, pairs changed 0
fullset, iterNUm: 7 i: 1488, pairs changed 0
fullset, iterNUm: 7 i: 1489, pairs changed 0
fullset, iterNUm: 7 i: 1490, pairs changed 0
fullset, iterNUm: 7 i: 1491, pairs changed 0
fullset, iterNUm: 7 i: 1492, pairs changed 0
fullset, iterNUm: 7 i: 1493, pairs changed 0
fullset, iterNUm: 7 i: 1494, pairs changed 0
fullset, iterNUm: 7 i: 1495, pairs changed 0
fullset, iterNUm: 7 i: 1496, pairs changed 0
fullset, iterNUm: 7 i: 1497, pairs changed 0
fullset, iterNUm: 7 i: 1498, pairs changed 0
fullset, iterNUm: 7 i: 1499, pairs changed 0
fullset, iterNUm: 7 i: 1500, pairs changed 0
fullset, iterNUm: 7 i: 1501, pairs changed 0
fullset, iterNUm: 7 i: 1502, pairs changed 0
fullset, iterNUm: 7 i: 1503, pairs changed 0
fullset, iterNUm: 7 i: 1504, pairs changed 0
fullset, iterNUm: 7 i: 1505, pairs changed 0
fullset, i

测试集错误率为:0.094080


In [17]:
testDigits(trainData,testData,('rbf',5))

L==H
fullset, iterNUm: 0 i: 0, pairs changed 0
fullset, iterNUm: 0 i: 1, pairs changed 1
fullset, iterNUm: 0 i: 2, pairs changed 2
fullset, iterNUm: 0 i: 3, pairs changed 3
fullset, iterNUm: 0 i: 4, pairs changed 4
fullset, iterNUm: 0 i: 5, pairs changed 5
fullset, iterNUm: 0 i: 6, pairs changed 6
fullset, iterNUm: 0 i: 7, pairs changed 7
fullset, iterNUm: 0 i: 8, pairs changed 8
fullset, iterNUm: 0 i: 9, pairs changed 9
fullset, iterNUm: 0 i: 10, pairs changed 10
fullset, iterNUm: 0 i: 11, pairs changed 11
fullset, iterNUm: 0 i: 12, pairs changed 12
fullset, iterNUm: 0 i: 13, pairs changed 13
fullset, iterNUm: 0 i: 14, pairs changed 14
fullset, iterNUm: 0 i: 15, pairs changed 15
fullset, iterNUm: 0 i: 16, pairs changed 16
fullset, iterNUm: 0 i: 17, pairs changed 17
fullset, iterNUm: 0 i: 18, pairs changed 18
fullset, iterNUm: 0 i: 19, pairs changed 19
fullset, iterNUm: 0 i: 20, pairs changed 20
fullset, iterNUm: 0 i: 21, pairs changed 21
fullset, iterNUm: 0 i: 22, pairs changed 22
ful

fullset, iterNUm: 0 i: 209, pairs changed 93
fullset, iterNUm: 0 i: 210, pairs changed 94
fullset, iterNUm: 0 i: 211, pairs changed 95
fullset, iterNUm: 0 i: 212, pairs changed 96
fullset, iterNUm: 0 i: 213, pairs changed 97
fullset, iterNUm: 0 i: 214, pairs changed 98
fullset, iterNUm: 0 i: 215, pairs changed 99
j not moving enough
fullset, iterNUm: 0 i: 216, pairs changed 99
fullset, iterNUm: 0 i: 217, pairs changed 100
fullset, iterNUm: 0 i: 218, pairs changed 101
j not moving enough
fullset, iterNUm: 0 i: 219, pairs changed 101
j not moving enough
fullset, iterNUm: 0 i: 220, pairs changed 101
fullset, iterNUm: 0 i: 221, pairs changed 102
j not moving enough
fullset, iterNUm: 0 i: 222, pairs changed 102
fullset, iterNUm: 0 i: 223, pairs changed 103
fullset, iterNUm: 0 i: 224, pairs changed 104
j not moving enough
fullset, iterNUm: 0 i: 225, pairs changed 104
j not moving enough
fullset, iterNUm: 0 i: 226, pairs changed 104
fullset, iterNUm: 0 i: 227, pairs changed 104
j not moving e

L==H
fullset, iterNUm: 0 i: 410, pairs changed 127
L==H
fullset, iterNUm: 0 i: 411, pairs changed 127
L==H
fullset, iterNUm: 0 i: 412, pairs changed 127
L==H
fullset, iterNUm: 0 i: 413, pairs changed 127
L==H
fullset, iterNUm: 0 i: 414, pairs changed 127
L==H
fullset, iterNUm: 0 i: 415, pairs changed 127
L==H
fullset, iterNUm: 0 i: 416, pairs changed 127
L==H
fullset, iterNUm: 0 i: 417, pairs changed 127
L==H
fullset, iterNUm: 0 i: 418, pairs changed 127
L==H
fullset, iterNUm: 0 i: 419, pairs changed 127
L==H
fullset, iterNUm: 0 i: 420, pairs changed 127
L==H
fullset, iterNUm: 0 i: 421, pairs changed 127
L==H
fullset, iterNUm: 0 i: 422, pairs changed 127
L==H
fullset, iterNUm: 0 i: 423, pairs changed 127
L==H
fullset, iterNUm: 0 i: 424, pairs changed 127
L==H
fullset, iterNUm: 0 i: 425, pairs changed 127
L==H
fullset, iterNUm: 0 i: 426, pairs changed 127
L==H
fullset, iterNUm: 0 i: 427, pairs changed 127
L==H
fullset, iterNUm: 0 i: 428, pairs changed 127
L==H
fullset, iterNUm: 0 i: 429

L==H
fullset, iterNUm: 0 i: 576, pairs changed 127
L==H
fullset, iterNUm: 0 i: 577, pairs changed 127
L==H
fullset, iterNUm: 0 i: 578, pairs changed 127
L==H
fullset, iterNUm: 0 i: 579, pairs changed 127
L==H
fullset, iterNUm: 0 i: 580, pairs changed 127
L==H
fullset, iterNUm: 0 i: 581, pairs changed 127
L==H
fullset, iterNUm: 0 i: 582, pairs changed 127
L==H
fullset, iterNUm: 0 i: 583, pairs changed 127
L==H
fullset, iterNUm: 0 i: 584, pairs changed 127
L==H
fullset, iterNUm: 0 i: 585, pairs changed 127
L==H
fullset, iterNUm: 0 i: 586, pairs changed 127
L==H
fullset, iterNUm: 0 i: 587, pairs changed 127
L==H
fullset, iterNUm: 0 i: 588, pairs changed 127
L==H
fullset, iterNUm: 0 i: 589, pairs changed 127
L==H
fullset, iterNUm: 0 i: 590, pairs changed 127
L==H
fullset, iterNUm: 0 i: 591, pairs changed 127
L==H
fullset, iterNUm: 0 i: 592, pairs changed 127
L==H
fullset, iterNUm: 0 i: 593, pairs changed 127
L==H
fullset, iterNUm: 0 i: 594, pairs changed 127
L==H
fullset, iterNUm: 0 i: 595

L==H
fullset, iterNUm: 0 i: 748, pairs changed 127
L==H
fullset, iterNUm: 0 i: 749, pairs changed 127
L==H
fullset, iterNUm: 0 i: 750, pairs changed 127
L==H
fullset, iterNUm: 0 i: 751, pairs changed 127
L==H
fullset, iterNUm: 0 i: 752, pairs changed 127
L==H
fullset, iterNUm: 0 i: 753, pairs changed 127
L==H
fullset, iterNUm: 0 i: 754, pairs changed 127
L==H
fullset, iterNUm: 0 i: 755, pairs changed 127
L==H
fullset, iterNUm: 0 i: 756, pairs changed 127
L==H
fullset, iterNUm: 0 i: 757, pairs changed 127
L==H
fullset, iterNUm: 0 i: 758, pairs changed 127
L==H
fullset, iterNUm: 0 i: 759, pairs changed 127
L==H
fullset, iterNUm: 0 i: 760, pairs changed 127
L==H
fullset, iterNUm: 0 i: 761, pairs changed 127
L==H
fullset, iterNUm: 0 i: 762, pairs changed 127
L==H
fullset, iterNUm: 0 i: 763, pairs changed 127
L==H
fullset, iterNUm: 0 i: 764, pairs changed 127
L==H
fullset, iterNUm: 0 i: 765, pairs changed 127
L==H
fullset, iterNUm: 0 i: 766, pairs changed 127
L==H
fullset, iterNUm: 0 i: 767

...

L==H
fullset, iterNUm: 8 i: 1209, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1210, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1211, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1212, pairs changed 0
fullset, iterNUm: 8 i: 1213, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1214, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1215, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1216, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1217, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1218, pairs changed 0
fullset, iterNUm: 8 i: 1219, pairs changed 0
fullset, iterNUm: 8 i: 1220, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1221, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1222, pairs changed 0
fullset, iterNUm: 8 i: 1223, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1224, pairs changed 0
fullset, iterNUm: 8 i: 1225, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1226, pairs changed 0
fullset, iterNUm: 8 i: 1227, pairs changed 0
fullset, iterNUm: 8 i: 1228, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1229, p

L==H
fullset, iterNUm: 8 i: 1383, pairs changed 0
fullset, iterNUm: 8 i: 1384, pairs changed 0
fullset, iterNUm: 8 i: 1385, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1386, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1387, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1388, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1389, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1390, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1391, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1392, pairs changed 0
fullset, iterNUm: 8 i: 1393, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1394, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1395, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1396, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1397, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1398, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1399, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1400, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1401, pairs changed 0
fulls

j not moving enough
fullset, iterNUm: 8 i: 1540, pairs changed 0
fullset, iterNUm: 8 i: 1541, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1542, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1543, pairs changed 0
fullset, iterNUm: 8 i: 1544, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1545, pairs changed 0
fullset, iterNUm: 8 i: 1546, pairs changed 0
fullset, iterNUm: 8 i: 1547, pairs changed 0
fullset, iterNUm: 8 i: 1548, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1549, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1550, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1551, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1552, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1553, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1554, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1555, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1556, pairs changed 0
fullset, iterNUm: 8 i: 1557, pairs changed 0
fullset, iterNUm: 8 i: 1558, pairs changed 0
fullset, i

j not moving enough
fullset, iterNUm: 8 i: 1691, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1692, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1693, pairs changed 0
fullset, iterNUm: 8 i: 1694, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1695, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1696, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1697, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1698, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1699, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1700, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1701, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1702, pairs changed 0
fullset, iterNUm: 8 i: 1703, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1704, pairs changed 0
fullset, iterNUm: 8 i: 1705, pairs changed 0
fullset, iterNUm: 8 i: 1706, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1707, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1708, p

fullset, iterNUm: 8 i: 1827, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1828, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1829, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1830, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1831, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1832, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1833, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1834, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1835, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1836, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1837, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1838, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1839, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1840, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1841, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 18

In [18]:
testDigits(trainData,testData,('rbf',10))

L==H
fullset, iterNUm: 0 i: 0, pairs changed 0
fullset, iterNUm: 0 i: 1, pairs changed 1
fullset, iterNUm: 0 i: 2, pairs changed 2
fullset, iterNUm: 0 i: 3, pairs changed 3
fullset, iterNUm: 0 i: 4, pairs changed 4
fullset, iterNUm: 0 i: 5, pairs changed 5
L==H
fullset, iterNUm: 0 i: 6, pairs changed 5
fullset, iterNUm: 0 i: 7, pairs changed 6
fullset, iterNUm: 0 i: 8, pairs changed 7
fullset, iterNUm: 0 i: 9, pairs changed 8
fullset, iterNUm: 0 i: 10, pairs changed 8
fullset, iterNUm: 0 i: 11, pairs changed 8
fullset, iterNUm: 0 i: 12, pairs changed 8
fullset, iterNUm: 0 i: 13, pairs changed 9
fullset, iterNUm: 0 i: 14, pairs changed 10
fullset, iterNUm: 0 i: 15, pairs changed 11
L==H
fullset, iterNUm: 0 i: 16, pairs changed 11
L==H
fullset, iterNUm: 0 i: 17, pairs changed 11
L==H
fullset, iterNUm: 0 i: 18, pairs changed 11
fullset, iterNUm: 0 i: 19, pairs changed 11
L==H
fullset, iterNUm: 0 i: 20, pairs changed 11
L==H
fullset, iterNUm: 0 i: 21, pairs changed 11
L==H
fullset, iterNUm

L==H
fullset, iterNUm: 0 i: 173, pairs changed 11
L==H
fullset, iterNUm: 0 i: 174, pairs changed 11
L==H
fullset, iterNUm: 0 i: 175, pairs changed 11
L==H
fullset, iterNUm: 0 i: 176, pairs changed 11
L==H
fullset, iterNUm: 0 i: 177, pairs changed 11
L==H
fullset, iterNUm: 0 i: 178, pairs changed 11
L==H
fullset, iterNUm: 0 i: 179, pairs changed 11
L==H
fullset, iterNUm: 0 i: 180, pairs changed 11
L==H
fullset, iterNUm: 0 i: 181, pairs changed 11
fullset, iterNUm: 0 i: 182, pairs changed 11
L==H
fullset, iterNUm: 0 i: 183, pairs changed 11
L==H
fullset, iterNUm: 0 i: 184, pairs changed 11
L==H
fullset, iterNUm: 0 i: 185, pairs changed 11
L==H
fullset, iterNUm: 0 i: 186, pairs changed 11
L==H
fullset, iterNUm: 0 i: 187, pairs changed 11
L==H
fullset, iterNUm: 0 i: 188, pairs changed 11
L==H
fullset, iterNUm: 0 i: 189, pairs changed 11
L==H
fullset, iterNUm: 0 i: 190, pairs changed 11
L==H
fullset, iterNUm: 0 i: 191, pairs changed 11
L==H
fullset, iterNUm: 0 i: 192, pairs changed 11
L==H


fullset, iterNUm: 0 i: 349, pairs changed 11
L==H
fullset, iterNUm: 0 i: 350, pairs changed 11
L==H
fullset, iterNUm: 0 i: 351, pairs changed 11
L==H
fullset, iterNUm: 0 i: 352, pairs changed 11
L==H
fullset, iterNUm: 0 i: 353, pairs changed 11
L==H
fullset, iterNUm: 0 i: 354, pairs changed 11
L==H
fullset, iterNUm: 0 i: 355, pairs changed 11
L==H
fullset, iterNUm: 0 i: 356, pairs changed 11
L==H
fullset, iterNUm: 0 i: 357, pairs changed 11
L==H
fullset, iterNUm: 0 i: 358, pairs changed 11
L==H
fullset, iterNUm: 0 i: 359, pairs changed 11
L==H
fullset, iterNUm: 0 i: 360, pairs changed 11
L==H
fullset, iterNUm: 0 i: 361, pairs changed 11
L==H
fullset, iterNUm: 0 i: 362, pairs changed 11
L==H
fullset, iterNUm: 0 i: 363, pairs changed 11
L==H
fullset, iterNUm: 0 i: 364, pairs changed 11
L==H
fullset, iterNUm: 0 i: 365, pairs changed 11
L==H
fullset, iterNUm: 0 i: 366, pairs changed 11
L==H
fullset, iterNUm: 0 i: 367, pairs changed 11
L==H
fullset, iterNUm: 0 i: 368, pairs changed 11
L==H


L==H
fullset, iterNUm: 0 i: 525, pairs changed 11
L==H
fullset, iterNUm: 0 i: 526, pairs changed 11
L==H
fullset, iterNUm: 0 i: 527, pairs changed 11
L==H
fullset, iterNUm: 0 i: 528, pairs changed 11
L==H
fullset, iterNUm: 0 i: 529, pairs changed 11
L==H
fullset, iterNUm: 0 i: 530, pairs changed 11
L==H
fullset, iterNUm: 0 i: 531, pairs changed 11
L==H
fullset, iterNUm: 0 i: 532, pairs changed 11
L==H
fullset, iterNUm: 0 i: 533, pairs changed 11
L==H
fullset, iterNUm: 0 i: 534, pairs changed 11
L==H
fullset, iterNUm: 0 i: 535, pairs changed 11
L==H
fullset, iterNUm: 0 i: 536, pairs changed 11
L==H
fullset, iterNUm: 0 i: 537, pairs changed 11
L==H
fullset, iterNUm: 0 i: 538, pairs changed 11
L==H
fullset, iterNUm: 0 i: 539, pairs changed 11
L==H
fullset, iterNUm: 0 i: 540, pairs changed 11
L==H
fullset, iterNUm: 0 i: 541, pairs changed 11
L==H
fullset, iterNUm: 0 i: 542, pairs changed 11
L==H
fullset, iterNUm: 0 i: 543, pairs changed 11
L==H
fullset, iterNUm: 0 i: 544, pairs changed 11


L==H
fullset, iterNUm: 0 i: 692, pairs changed 11
L==H
fullset, iterNUm: 0 i: 693, pairs changed 11
L==H
fullset, iterNUm: 0 i: 694, pairs changed 11
L==H
fullset, iterNUm: 0 i: 695, pairs changed 11
L==H
fullset, iterNUm: 0 i: 696, pairs changed 11
L==H
fullset, iterNUm: 0 i: 697, pairs changed 11
L==H
fullset, iterNUm: 0 i: 698, pairs changed 11
L==H
fullset, iterNUm: 0 i: 699, pairs changed 11
L==H
fullset, iterNUm: 0 i: 700, pairs changed 11
L==H
fullset, iterNUm: 0 i: 701, pairs changed 11
L==H
fullset, iterNUm: 0 i: 702, pairs changed 11
L==H
fullset, iterNUm: 0 i: 703, pairs changed 11
L==H
fullset, iterNUm: 0 i: 704, pairs changed 11
L==H
fullset, iterNUm: 0 i: 705, pairs changed 11
L==H
fullset, iterNUm: 0 i: 706, pairs changed 11
L==H
fullset, iterNUm: 0 i: 707, pairs changed 11
L==H
fullset, iterNUm: 0 i: 708, pairs changed 11
L==H
fullset, iterNUm: 0 i: 709, pairs changed 11
L==H
fullset, iterNUm: 0 i: 710, pairs changed 11
L==H
fullset, iterNUm: 0 i: 711, pairs changed 11


...

L==H
fullset, iterNUm: 8 i: 1085, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1086, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1087, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1088, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1089, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1090, pairs changed 0
fullset, iterNUm: 8 i: 1091, pairs changed 0
fullset, iterNUm: 8 i: 1092, pairs changed 0
fullset, iterNUm: 8 i: 1093, pairs changed 0
fullset, iterNUm: 8 i: 1094, pairs changed 0
fullset, iterNUm: 8 i: 1095, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1096, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1097, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1098, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1099, pairs changed 0
fullset, iterNUm: 8 i: 1100, pairs changed 0
fullset, iterNUm: 8 i: 1101, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1102, pairs changed 0
fullset, iterNUm: 8 i: 1103, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1104, pairs changed 0
fullset, i

L==H
fullset, iterNUm: 8 i: 1361, pairs changed 0
fullset, iterNUm: 8 i: 1362, pairs changed 0
fullset, iterNUm: 8 i: 1363, pairs changed 0
fullset, iterNUm: 8 i: 1364, pairs changed 0
fullset, iterNUm: 8 i: 1365, pairs changed 0
fullset, iterNUm: 8 i: 1366, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1367, pairs changed 0
fullset, iterNUm: 8 i: 1368, pairs changed 0
fullset, iterNUm: 8 i: 1369, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1370, pairs changed 0
fullset, iterNUm: 8 i: 1371, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1372, pairs changed 0
fullset, iterNUm: 8 i: 1373, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1374, pairs changed 0
fullset, iterNUm: 8 i: 1375, pairs changed 0
fullset, iterNUm: 8 i: 1376, pairs changed 0
fullset, iterNUm: 8 i: 1377, pairs changed 0
fullset, iterNUm: 8 i: 1378, pairs changed 0
fullset, iterNUm: 8 i: 1379, pairs changed 0
fullset, iterNUm: 8 i: 1380, pairs changed 0
fullset, iterNUm: 8 i: 1381, pairs changed 0


j not moving enough
fullset, iterNUm: 8 i: 1551, pairs changed 0
fullset, iterNUm: 8 i: 1552, pairs changed 0
fullset, iterNUm: 8 i: 1553, pairs changed 0
fullset, iterNUm: 8 i: 1554, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1555, pairs changed 0
fullset, iterNUm: 8 i: 1556, pairs changed 0
fullset, iterNUm: 8 i: 1557, pairs changed 0
fullset, iterNUm: 8 i: 1558, pairs changed 0
fullset, iterNUm: 8 i: 1559, pairs changed 0
fullset, iterNUm: 8 i: 1560, pairs changed 0
fullset, iterNUm: 8 i: 1561, pairs changed 0
fullset, iterNUm: 8 i: 1562, pairs changed 0
fullset, iterNUm: 8 i: 1563, pairs changed 0
fullset, iterNUm: 8 i: 1564, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1565, pairs changed 0
fullset, iterNUm: 8 i: 1566, pairs changed 0
fullset, iterNUm: 8 i: 1567, pairs changed 0
fullset, iterNUm: 8 i: 1568, pairs changed 0
fullset, iterNUm: 8 i: 1569, pairs changed 0
fullset, iterNUm: 8 i: 1570, pairs changed 0
fullset, iterNUm: 8 i: 1571, pairs changed 0
L==H
fullset, iterNUm: 8 

L==H
fullset, iterNUm: 8 i: 1726, pairs changed 0
fullset, iterNUm: 8 i: 1727, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1728, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1729, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1730, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1731, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1732, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1733, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1734, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1735, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1736, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1737, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1738, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1739, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1740, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1741, pairs changed 0
j not moving enough
fulls

j not moving enough
fullset, iterNUm: 8 i: 1863, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1864, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1865, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1866, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1867, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1868, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1869, pairs changed 0
fullset, iterNUm: 8 i: 1870, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1871, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1872, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1873, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1874, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1875, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1876, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1877, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 18

In [19]:
testDigits(trainData,testData,('rbf',50))

L==H
fullset, iterNUm: 0 i: 0, pairs changed 0
fullset, iterNUm: 0 i: 1, pairs changed 1
fullset, iterNUm: 0 i: 2, pairs changed 2
fullset, iterNUm: 0 i: 3, pairs changed 3
fullset, iterNUm: 0 i: 4, pairs changed 4
fullset, iterNUm: 0 i: 5, pairs changed 4
fullset, iterNUm: 0 i: 6, pairs changed 4
fullset, iterNUm: 0 i: 7, pairs changed 5
fullset, iterNUm: 0 i: 8, pairs changed 6
fullset, iterNUm: 0 i: 9, pairs changed 7
fullset, iterNUm: 0 i: 10, pairs changed 7
fullset, iterNUm: 0 i: 11, pairs changed 7
fullset, iterNUm: 0 i: 12, pairs changed 7
fullset, iterNUm: 0 i: 13, pairs changed 8
fullset, iterNUm: 0 i: 14, pairs changed 8
fullset, iterNUm: 0 i: 15, pairs changed 8
fullset, iterNUm: 0 i: 16, pairs changed 8
fullset, iterNUm: 0 i: 17, pairs changed 8
fullset, iterNUm: 0 i: 18, pairs changed 8
fullset, iterNUm: 0 i: 19, pairs changed 8
fullset, iterNUm: 0 i: 20, pairs changed 8
fullset, iterNUm: 0 i: 21, pairs changed 8
L==H
fullset, iterNUm: 0 i: 22, pairs changed 8
fullset, it

L==H
fullset, iterNUm: 0 i: 247, pairs changed 8
L==H
fullset, iterNUm: 0 i: 248, pairs changed 8
L==H
fullset, iterNUm: 0 i: 249, pairs changed 8
L==H
fullset, iterNUm: 0 i: 250, pairs changed 8
L==H
fullset, iterNUm: 0 i: 251, pairs changed 8
fullset, iterNUm: 0 i: 252, pairs changed 8
L==H
fullset, iterNUm: 0 i: 253, pairs changed 8
L==H
fullset, iterNUm: 0 i: 254, pairs changed 8
L==H
fullset, iterNUm: 0 i: 255, pairs changed 8
L==H
fullset, iterNUm: 0 i: 256, pairs changed 8
L==H
fullset, iterNUm: 0 i: 257, pairs changed 8
L==H
fullset, iterNUm: 0 i: 258, pairs changed 8
L==H
fullset, iterNUm: 0 i: 259, pairs changed 8
L==H
fullset, iterNUm: 0 i: 260, pairs changed 8
L==H
fullset, iterNUm: 0 i: 261, pairs changed 8
L==H
fullset, iterNUm: 0 i: 262, pairs changed 8
L==H
fullset, iterNUm: 0 i: 263, pairs changed 8
L==H
fullset, iterNUm: 0 i: 264, pairs changed 8
L==H
fullset, iterNUm: 0 i: 265, pairs changed 8
L==H
fullset, iterNUm: 0 i: 266, pairs changed 8
L==H
fullset, iterNUm: 0 

L==H
fullset, iterNUm: 0 i: 426, pairs changed 8
L==H
fullset, iterNUm: 0 i: 427, pairs changed 8
L==H
fullset, iterNUm: 0 i: 428, pairs changed 8
L==H
fullset, iterNUm: 0 i: 429, pairs changed 8
L==H
fullset, iterNUm: 0 i: 430, pairs changed 8
L==H
fullset, iterNUm: 0 i: 431, pairs changed 8
L==H
fullset, iterNUm: 0 i: 432, pairs changed 8
L==H
fullset, iterNUm: 0 i: 433, pairs changed 8
L==H
fullset, iterNUm: 0 i: 434, pairs changed 8
L==H
fullset, iterNUm: 0 i: 435, pairs changed 8
L==H
fullset, iterNUm: 0 i: 436, pairs changed 8
L==H
fullset, iterNUm: 0 i: 437, pairs changed 8
L==H
fullset, iterNUm: 0 i: 438, pairs changed 8
L==H
fullset, iterNUm: 0 i: 439, pairs changed 8
L==H
fullset, iterNUm: 0 i: 440, pairs changed 8
L==H
fullset, iterNUm: 0 i: 441, pairs changed 8
L==H
fullset, iterNUm: 0 i: 442, pairs changed 8
L==H
fullset, iterNUm: 0 i: 443, pairs changed 8
L==H
fullset, iterNUm: 0 i: 444, pairs changed 8
L==H
fullset, iterNUm: 0 i: 445, pairs changed 8
L==H
fullset, iterNU

L==H
fullset, iterNUm: 0 i: 596, pairs changed 8
L==H
fullset, iterNUm: 0 i: 597, pairs changed 8
L==H
fullset, iterNUm: 0 i: 598, pairs changed 8
L==H
fullset, iterNUm: 0 i: 599, pairs changed 8
L==H
fullset, iterNUm: 0 i: 600, pairs changed 8
L==H
fullset, iterNUm: 0 i: 601, pairs changed 8
L==H
fullset, iterNUm: 0 i: 602, pairs changed 8
L==H
fullset, iterNUm: 0 i: 603, pairs changed 8
L==H
fullset, iterNUm: 0 i: 604, pairs changed 8
L==H
fullset, iterNUm: 0 i: 605, pairs changed 8
L==H
fullset, iterNUm: 0 i: 606, pairs changed 8
L==H
fullset, iterNUm: 0 i: 607, pairs changed 8
L==H
fullset, iterNUm: 0 i: 608, pairs changed 8
L==H
fullset, iterNUm: 0 i: 609, pairs changed 8
L==H
fullset, iterNUm: 0 i: 610, pairs changed 8
L==H
fullset, iterNUm: 0 i: 611, pairs changed 8
L==H
fullset, iterNUm: 0 i: 612, pairs changed 8
L==H
fullset, iterNUm: 0 i: 613, pairs changed 8
L==H
fullset, iterNUm: 0 i: 614, pairs changed 8
L==H
fullset, iterNUm: 0 i: 615, pairs changed 8
L==H
fullset, iterNU

L==H
fullset, iterNUm: 0 i: 766, pairs changed 8
L==H
fullset, iterNUm: 0 i: 767, pairs changed 8
fullset, iterNUm: 0 i: 768, pairs changed 8
L==H
fullset, iterNUm: 0 i: 769, pairs changed 8
L==H
fullset, iterNUm: 0 i: 770, pairs changed 8
L==H
fullset, iterNUm: 0 i: 771, pairs changed 8
L==H
fullset, iterNUm: 0 i: 772, pairs changed 8
L==H
fullset, iterNUm: 0 i: 773, pairs changed 8
L==H
fullset, iterNUm: 0 i: 774, pairs changed 8
L==H
fullset, iterNUm: 0 i: 775, pairs changed 8
L==H
fullset, iterNUm: 0 i: 776, pairs changed 8
L==H
fullset, iterNUm: 0 i: 777, pairs changed 8
L==H
fullset, iterNUm: 0 i: 778, pairs changed 8
L==H
fullset, iterNUm: 0 i: 779, pairs changed 8
L==H
fullset, iterNUm: 0 i: 780, pairs changed 8
L==H
fullset, iterNUm: 0 i: 781, pairs changed 8
L==H
fullset, iterNUm: 0 i: 782, pairs changed 8
fullset, iterNUm: 0 i: 783, pairs changed 8
L==H
fullset, iterNUm: 0 i: 784, pairs changed 8
L==H
fullset, iterNUm: 0 i: 785, pairs changed 8
L==H
fullset, iterNUm: 0 i: 78

...

L==H
fullset, iterNUm: 7 i: 1096, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1097, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1098, pairs changed 0
fullset, iterNUm: 7 i: 1099, pairs changed 0
fullset, iterNUm: 7 i: 1100, pairs changed 0
fullset, iterNUm: 7 i: 1101, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1102, pairs changed 0
fullset, iterNUm: 7 i: 1103, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1104, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1105, pairs changed 0
fullset, iterNUm: 7 i: 1106, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1107, pairs changed 0
j not moving enough
fullset, iterNUm: 7 i: 1108, pairs changed 0
fullset, iterNUm: 7 i: 1109, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1110, pairs changed 0
j not moving enough
fullset, iterNUm: 7 i: 1111, pairs changed 0
j not moving enough
fullset, iterNUm: 7 i: 1112, pairs changed 0
fullset, iterNUm: 7 i: 1113, pairs changed 0
fullset, iterNUm: 7 i: 1114, pairs changed 0
fullset, iterNUm: 7 i: 1115, pairs changed 0


L==H
fullset, iterNUm: 7 i: 1350, pairs changed 0
fullset, iterNUm: 7 i: 1351, pairs changed 0
fullset, iterNUm: 7 i: 1352, pairs changed 0
fullset, iterNUm: 7 i: 1353, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1354, pairs changed 0
fullset, iterNUm: 7 i: 1355, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1356, pairs changed 0
fullset, iterNUm: 7 i: 1357, pairs changed 0
j not moving enough
fullset, iterNUm: 7 i: 1358, pairs changed 0
fullset, iterNUm: 7 i: 1359, pairs changed 0
fullset, iterNUm: 7 i: 1360, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1361, pairs changed 0
fullset, iterNUm: 7 i: 1362, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1363, pairs changed 0
fullset, iterNUm: 7 i: 1364, pairs changed 0
fullset, iterNUm: 7 i: 1365, pairs changed 0
fullset, iterNUm: 7 i: 1366, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1367, pairs changed 0
fullset, iterNUm: 7 i: 1368, pairs changed 0
fullset, iterNUm: 7 i: 1369, pairs changed 0
j not moving enough
fullset, iterNUm: 7 i: 1370, p

L==H
fullset, iterNUm: 7 i: 1528, pairs changed 0
fullset, iterNUm: 7 i: 1529, pairs changed 0
fullset, iterNUm: 7 i: 1530, pairs changed 0
fullset, iterNUm: 7 i: 1531, pairs changed 0
fullset, iterNUm: 7 i: 1532, pairs changed 0
fullset, iterNUm: 7 i: 1533, pairs changed 0
fullset, iterNUm: 7 i: 1534, pairs changed 0
fullset, iterNUm: 7 i: 1535, pairs changed 0
fullset, iterNUm: 7 i: 1536, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1537, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1538, pairs changed 0
fullset, iterNUm: 7 i: 1539, pairs changed 0
j not moving enough
fullset, iterNUm: 7 i: 1540, pairs changed 0
fullset, iterNUm: 7 i: 1541, pairs changed 0
fullset, iterNUm: 7 i: 1542, pairs changed 0
fullset, iterNUm: 7 i: 1543, pairs changed 0
fullset, iterNUm: 7 i: 1544, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1545, pairs changed 0
fullset, iterNUm: 7 i: 1546, pairs changed 0
fullset, iterNUm: 7 i: 1547, pairs changed 0
fullset, iterNUm: 7 i: 1548, pairs changed 0
fullset, iterNU

L==H
fullset, iterNUm: 7 i: 1707, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1708, pairs changed 0
fullset, iterNUm: 7 i: 1709, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1710, pairs changed 0
fullset, iterNUm: 7 i: 1711, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1712, pairs changed 0
fullset, iterNUm: 7 i: 1713, pairs changed 0
fullset, iterNUm: 7 i: 1714, pairs changed 0
fullset, iterNUm: 7 i: 1715, pairs changed 0
fullset, iterNUm: 7 i: 1716, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1717, pairs changed 0
fullset, iterNUm: 7 i: 1718, pairs changed 0
fullset, iterNUm: 7 i: 1719, pairs changed 0
j not moving enough
fullset, iterNUm: 7 i: 1720, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1721, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1722, pairs changed 0
L==H
fullset, iterNUm: 7 i: 1723, pairs changed 0
fullset, iterNUm: 7 i: 1724, pairs changed 0
fullset, iterNUm: 7 i: 1725, pairs changed 0
fullset, iterNUm: 7 i: 1726, pairs changed 0
fullset, iterNUm: 7 i: 1727, pairs chang

j not moving enough
fullset, iterNUm: 7 i: 1846, pairs changed 0
j not moving enough
fullset, iterNUm: 7 i: 1847, pairs changed 0
j not moving enough
fullset, iterNUm: 7 i: 1848, pairs changed 0
j not moving enough
fullset, iterNUm: 7 i: 1849, pairs changed 0
j not moving enough
fullset, iterNUm: 7 i: 1850, pairs changed 0
j not moving enough
fullset, iterNUm: 7 i: 1851, pairs changed 0
j not moving enough
fullset, iterNUm: 7 i: 1852, pairs changed 0
j not moving enough
fullset, iterNUm: 7 i: 1853, pairs changed 0
fullset, iterNUm: 7 i: 1854, pairs changed 0
fullset, iterNUm: 7 i: 1855, pairs changed 0
j not moving enough
fullset, iterNUm: 7 i: 1856, pairs changed 0
j not moving enough
fullset, iterNUm: 7 i: 1857, pairs changed 0
fullset, iterNUm: 7 i: 1858, pairs changed 0
j not moving enough
fullset, iterNUm: 7 i: 1859, pairs changed 0
j not moving enough
fullset, iterNUm: 7 i: 1860, pairs changed 0
fullset, iterNUm: 7 i: 1861, pairs changed 0
j not moving enough
fullset, iterNUm: 7 

In [21]:
testDigits(trainData,testData,('lin',))

L==H
fullset, iterNUm: 0 i: 0, pairs changed 0
fullset, iterNUm: 0 i: 1, pairs changed 1
fullset, iterNUm: 0 i: 2, pairs changed 2
fullset, iterNUm: 0 i: 3, pairs changed 3
fullset, iterNUm: 0 i: 4, pairs changed 4
fullset, iterNUm: 0 i: 5, pairs changed 4
fullset, iterNUm: 0 i: 6, pairs changed 4
fullset, iterNUm: 0 i: 7, pairs changed 5
fullset, iterNUm: 0 i: 8, pairs changed 6
fullset, iterNUm: 0 i: 9, pairs changed 7
fullset, iterNUm: 0 i: 10, pairs changed 7
fullset, iterNUm: 0 i: 11, pairs changed 7
fullset, iterNUm: 0 i: 12, pairs changed 7
fullset, iterNUm: 0 i: 13, pairs changed 8
fullset, iterNUm: 0 i: 14, pairs changed 8
fullset, iterNUm: 0 i: 15, pairs changed 8
fullset, iterNUm: 0 i: 16, pairs changed 8
fullset, iterNUm: 0 i: 17, pairs changed 8
fullset, iterNUm: 0 i: 18, pairs changed 8
fullset, iterNUm: 0 i: 19, pairs changed 8
fullset, iterNUm: 0 i: 20, pairs changed 8
fullset, iterNUm: 0 i: 21, pairs changed 8
L==H
fullset, iterNUm: 0 i: 22, pairs changed 8
fullset, it

L==H
fullset, iterNUm: 0 i: 244, pairs changed 8
L==H
fullset, iterNUm: 0 i: 245, pairs changed 8
fullset, iterNUm: 0 i: 246, pairs changed 8
L==H
fullset, iterNUm: 0 i: 247, pairs changed 8
L==H
fullset, iterNUm: 0 i: 248, pairs changed 8
L==H
fullset, iterNUm: 0 i: 249, pairs changed 8
L==H
fullset, iterNUm: 0 i: 250, pairs changed 8
L==H
fullset, iterNUm: 0 i: 251, pairs changed 8
fullset, iterNUm: 0 i: 252, pairs changed 8
L==H
fullset, iterNUm: 0 i: 253, pairs changed 8
L==H
fullset, iterNUm: 0 i: 254, pairs changed 8
L==H
fullset, iterNUm: 0 i: 255, pairs changed 8
L==H
fullset, iterNUm: 0 i: 256, pairs changed 8
L==H
fullset, iterNUm: 0 i: 257, pairs changed 8
L==H
fullset, iterNUm: 0 i: 258, pairs changed 8
L==H
fullset, iterNUm: 0 i: 259, pairs changed 8
L==H
fullset, iterNUm: 0 i: 260, pairs changed 8
L==H
fullset, iterNUm: 0 i: 261, pairs changed 8
L==H
fullset, iterNUm: 0 i: 262, pairs changed 8
L==H
fullset, iterNUm: 0 i: 263, pairs changed 8
L==H
fullset, iterNUm: 0 i: 26

L==H
fullset, iterNUm: 0 i: 431, pairs changed 8
L==H
fullset, iterNUm: 0 i: 432, pairs changed 8
L==H
fullset, iterNUm: 0 i: 433, pairs changed 8
L==H
fullset, iterNUm: 0 i: 434, pairs changed 8
L==H
fullset, iterNUm: 0 i: 435, pairs changed 8
L==H
fullset, iterNUm: 0 i: 436, pairs changed 8
L==H
fullset, iterNUm: 0 i: 437, pairs changed 8
L==H
fullset, iterNUm: 0 i: 438, pairs changed 8
L==H
fullset, iterNUm: 0 i: 439, pairs changed 8
L==H
fullset, iterNUm: 0 i: 440, pairs changed 8
L==H
fullset, iterNUm: 0 i: 441, pairs changed 8
L==H
fullset, iterNUm: 0 i: 442, pairs changed 8
L==H
fullset, iterNUm: 0 i: 443, pairs changed 8
L==H
fullset, iterNUm: 0 i: 444, pairs changed 8
L==H
fullset, iterNUm: 0 i: 445, pairs changed 8
L==H
fullset, iterNUm: 0 i: 446, pairs changed 8
L==H
fullset, iterNUm: 0 i: 447, pairs changed 8
L==H
fullset, iterNUm: 0 i: 448, pairs changed 8
L==H
fullset, iterNUm: 0 i: 449, pairs changed 8
L==H
fullset, iterNUm: 0 i: 450, pairs changed 8
L==H
fullset, iterNU

L==H
fullset, iterNUm: 0 i: 604, pairs changed 8
L==H
fullset, iterNUm: 0 i: 605, pairs changed 8
L==H
fullset, iterNUm: 0 i: 606, pairs changed 8
L==H
fullset, iterNUm: 0 i: 607, pairs changed 8
L==H
fullset, iterNUm: 0 i: 608, pairs changed 8
L==H
fullset, iterNUm: 0 i: 609, pairs changed 8
L==H
fullset, iterNUm: 0 i: 610, pairs changed 8
L==H
fullset, iterNUm: 0 i: 611, pairs changed 8
L==H
fullset, iterNUm: 0 i: 612, pairs changed 8
L==H
fullset, iterNUm: 0 i: 613, pairs changed 8
L==H
fullset, iterNUm: 0 i: 614, pairs changed 8
L==H
fullset, iterNUm: 0 i: 615, pairs changed 8
L==H
fullset, iterNUm: 0 i: 616, pairs changed 8
L==H
fullset, iterNUm: 0 i: 617, pairs changed 8
L==H
fullset, iterNUm: 0 i: 618, pairs changed 8
L==H
fullset, iterNUm: 0 i: 619, pairs changed 8
L==H
fullset, iterNUm: 0 i: 620, pairs changed 8
L==H
fullset, iterNUm: 0 i: 621, pairs changed 8
L==H
fullset, iterNUm: 0 i: 622, pairs changed 8
L==H
fullset, iterNUm: 0 i: 623, pairs changed 8
L==H
fullset, iterNU

L==H
fullset, iterNUm: 0 i: 773, pairs changed 8
L==H
fullset, iterNUm: 0 i: 774, pairs changed 8
L==H
fullset, iterNUm: 0 i: 775, pairs changed 8
L==H
fullset, iterNUm: 0 i: 776, pairs changed 8
L==H
fullset, iterNUm: 0 i: 777, pairs changed 8
L==H
fullset, iterNUm: 0 i: 778, pairs changed 8
L==H
fullset, iterNUm: 0 i: 779, pairs changed 8
L==H
fullset, iterNUm: 0 i: 780, pairs changed 8
L==H
fullset, iterNUm: 0 i: 781, pairs changed 8
L==H
fullset, iterNUm: 0 i: 782, pairs changed 8
fullset, iterNUm: 0 i: 783, pairs changed 8
L==H
fullset, iterNUm: 0 i: 784, pairs changed 8
L==H
fullset, iterNUm: 0 i: 785, pairs changed 8
fullset, iterNUm: 0 i: 786, pairs changed 8
L==H
fullset, iterNUm: 0 i: 787, pairs changed 8
L==H
fullset, iterNUm: 0 i: 788, pairs changed 8
L==H
fullset, iterNUm: 0 i: 789, pairs changed 8
L==H
fullset, iterNUm: 0 i: 790, pairs changed 8
L==H
fullset, iterNUm: 0 i: 791, pairs changed 8
L==H
fullset, iterNUm: 0 i: 792, pairs changed 8
L==H
fullset, iterNUm: 0 i: 79

...

j not moving enough
fullset, iterNUm: 8 i: 760, pairs changed 0
fullset, iterNUm: 8 i: 761, pairs changed 0
fullset, iterNUm: 8 i: 762, pairs changed 0
fullset, iterNUm: 8 i: 763, pairs changed 0
fullset, iterNUm: 8 i: 764, pairs changed 0
fullset, iterNUm: 8 i: 765, pairs changed 0
fullset, iterNUm: 8 i: 766, pairs changed 0
fullset, iterNUm: 8 i: 767, pairs changed 0
fullset, iterNUm: 8 i: 768, pairs changed 0
fullset, iterNUm: 8 i: 769, pairs changed 0
fullset, iterNUm: 8 i: 770, pairs changed 0
fullset, iterNUm: 8 i: 771, pairs changed 0
fullset, iterNUm: 8 i: 772, pairs changed 0
fullset, iterNUm: 8 i: 773, pairs changed 0
fullset, iterNUm: 8 i: 774, pairs changed 0
fullset, iterNUm: 8 i: 775, pairs changed 0
fullset, iterNUm: 8 i: 776, pairs changed 0
fullset, iterNUm: 8 i: 777, pairs changed 0
fullset, iterNUm: 8 i: 778, pairs changed 0
fullset, iterNUm: 8 i: 779, pairs changed 0
fullset, iterNUm: 8 i: 780, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 781, pairs ch

j not moving enough
fullset, iterNUm: 8 i: 1003, pairs changed 0
fullset, iterNUm: 8 i: 1004, pairs changed 0
fullset, iterNUm: 8 i: 1005, pairs changed 0
fullset, iterNUm: 8 i: 1006, pairs changed 0
fullset, iterNUm: 8 i: 1007, pairs changed 0
fullset, iterNUm: 8 i: 1008, pairs changed 0
fullset, iterNUm: 8 i: 1009, pairs changed 0
fullset, iterNUm: 8 i: 1010, pairs changed 0
fullset, iterNUm: 8 i: 1011, pairs changed 0
fullset, iterNUm: 8 i: 1012, pairs changed 0
fullset, iterNUm: 8 i: 1013, pairs changed 0
fullset, iterNUm: 8 i: 1014, pairs changed 0
fullset, iterNUm: 8 i: 1015, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1016, pairs changed 0
fullset, iterNUm: 8 i: 1017, pairs changed 0
fullset, iterNUm: 8 i: 1018, pairs changed 0
fullset, iterNUm: 8 i: 1019, pairs changed 0
fullset, iterNUm: 8 i: 1020, pairs changed 0
fullset, iterNUm: 8 i: 1021, pairs changed 0
fullset, iterNUm: 8 i: 1022, pairs changed 0
fullset, iterNUm: 8 i: 1023, pairs changed 0
fullset, iterNU

j not moving enough
fullset, iterNUm: 8 i: 1370, pairs changed 0
fullset, iterNUm: 8 i: 1371, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1372, pairs changed 0
fullset, iterNUm: 8 i: 1373, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1374, pairs changed 0
fullset, iterNUm: 8 i: 1375, pairs changed 0
fullset, iterNUm: 8 i: 1376, pairs changed 0
fullset, iterNUm: 8 i: 1377, pairs changed 0
fullset, iterNUm: 8 i: 1378, pairs changed 0
fullset, iterNUm: 8 i: 1379, pairs changed 0
fullset, iterNUm: 8 i: 1380, pairs changed 0
fullset, iterNUm: 8 i: 1381, pairs changed 0
fullset, iterNUm: 8 i: 1382, pairs changed 0
fullset, iterNUm: 8 i: 1383, pairs changed 0
fullset, iterNUm: 8 i: 1384, pairs changed 0
fullset, iterNUm: 8 i: 1385, pairs changed 0
fullset, iterNUm: 8 i: 1386, pairs changed 0
fullset, iterNUm: 8 i: 1387, pairs changed 0
fullset, iterNUm: 8 i: 1388, pairs changed 0
fullset, iterNUm: 8 i: 1389, pairs changed 0
j not moving enough
fullset, iterNUm: 8 

j not moving enough
fullset, iterNUm: 8 i: 1663, pairs changed 0
fullset, iterNUm: 8 i: 1664, pairs changed 0
fullset, iterNUm: 8 i: 1665, pairs changed 0
fullset, iterNUm: 8 i: 1666, pairs changed 0
fullset, iterNUm: 8 i: 1667, pairs changed 0
fullset, iterNUm: 8 i: 1668, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1669, pairs changed 0
fullset, iterNUm: 8 i: 1670, pairs changed 0
fullset, iterNUm: 8 i: 1671, pairs changed 0
fullset, iterNUm: 8 i: 1672, pairs changed 0
fullset, iterNUm: 8 i: 1673, pairs changed 0
fullset, iterNUm: 8 i: 1674, pairs changed 0
fullset, iterNUm: 8 i: 1675, pairs changed 0
fullset, iterNUm: 8 i: 1676, pairs changed 0
fullset, iterNUm: 8 i: 1677, pairs changed 0
fullset, iterNUm: 8 i: 1678, pairs changed 0
fullset, iterNUm: 8 i: 1679, pairs changed 0
fullset, iterNUm: 8 i: 1680, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1681, pairs changed 0
fullset, iterNUm: 8 i: 1682, pairs changed 0
j not moving enough
fullset, iterNUm: 8 

j not moving enough
fullset, iterNUm: 8 i: 1808, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1809, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1810, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1811, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1812, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1813, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1814, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1815, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1816, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1817, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1818, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1819, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1820, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1821, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1822, pairs changed 0
j not moving enough
fulls

In [22]:
# 多分类算法
# 一对多法 one-vs-all

In [23]:
trainDataMulit = loadImages1('./digits/trainingDigits/')
testDataMulit = loadImages1('./digits/testDigits/')

In [27]:
def testDigitsMulit(trainData,testData,kTup=('rbf',10)):
    predict1 = np.mat(np.zeros(trainData[1].shape))
    predict2 = np.mat(np.zeros(testData[1].shape))
    errorCountTotal =  np.zeros(10)
    errorCountTotal2 =  np.zeros(10)
    for j in range(10):
        dataArr = trainData[0]
        labelArr = trainData[1][j,:]
        b,alphas = smoP(dataArr,labelArr,200,0.0001,10000,kTup)
        dataMat = np.mat(dataArr)
        labelMat = np.mat(labelArr).transpose()
        svInd = np.nonzero(alphas.A>0)[0]
        sVs = dataMat[svInd]
        labelSV = labelMat[svInd]
        print('支持向量数: %d'%np.shape(sVs)[0])
        m,n = np.shape(dataMat)
        errorCount = 0
        for i in range(m):
            kernelEval = kernelTrans(sVs,dataMat[i,:],kTup) # 挑出alphas非零的数据，因为其他数据即使做了核变换最后也会变成0
            predict1[j,i] = kernelEval.T * np.multiply(labelSV,alphas[svInd])+b
            if np.sign(predict1[j,i]) != np.sign(labelArr[0,i]):errorCount += 1
#             print("%f,%f"%(np.sign(predict1[j,i]),np.sign(labelArr[0,i])))  
        errorCountTotal[j] += errorCount/m
        print('训练集数字%d错误率为:%f'%(j,errorCount/m))
        
        dataArr2 = testData[0]
        labelArr2 =testData[1][j,:]
        dataMat2 = np.mat(dataArr2)
        labelMat2 = np.mat(labelArr2).transpose()
        m2,n2 = np.shape(dataMat2)
        errorCount2 = 0
        for i in range(m2):
            kernelEval = kernelTrans(sVs,dataMat2[i,:],kTup) # 挑出alphas非零的数据，因为其他数据即使做了核变换最后也会变成0,s所以只需要和支持向量乘就可以了
            predict2[j,i] = kernelEval.T * np.multiply(labelSV,alphas[svInd])+b
            if np.sign(predict2[j,i]) != np.sign(labelArr2[0,i]):
                errorCount2 += 1
        print('测试集数字%d错误率为:%f'%(j,errorCount2/m2))
        errorCountTotal2[j] += errorCount2/m2
    print('训练集总错误率为:%f'%(np.mean(errorCountTotal)))
    print('测试集总错误率为:%f'%(np.mean(errorCountTotal2)))

In [28]:
testDigitsMulit(trainDataMulit,testDataMulit,('rbf',10))

fullset, iterNUm: 0 i: 0, pairs changed 1
fullset, iterNUm: 0 i: 1, pairs changed 2
fullset, iterNUm: 0 i: 2, pairs changed 3
fullset, iterNUm: 0 i: 3, pairs changed 4
fullset, iterNUm: 0 i: 4, pairs changed 5
fullset, iterNUm: 0 i: 5, pairs changed 6
fullset, iterNUm: 0 i: 6, pairs changed 6
fullset, iterNUm: 0 i: 7, pairs changed 7
fullset, iterNUm: 0 i: 8, pairs changed 8
fullset, iterNUm: 0 i: 9, pairs changed 9
fullset, iterNUm: 0 i: 10, pairs changed 9
fullset, iterNUm: 0 i: 11, pairs changed 9
fullset, iterNUm: 0 i: 12, pairs changed 9
fullset, iterNUm: 0 i: 13, pairs changed 9
fullset, iterNUm: 0 i: 14, pairs changed 9
fullset, iterNUm: 0 i: 15, pairs changed 9
fullset, iterNUm: 0 i: 16, pairs changed 9
fullset, iterNUm: 0 i: 17, pairs changed 9
fullset, iterNUm: 0 i: 18, pairs changed 10
fullset, iterNUm: 0 i: 19, pairs changed 10
fullset, iterNUm: 0 i: 20, pairs changed 10
fullset, iterNUm: 0 i: 21, pairs changed 11
j not moving enough
fullset, iterNUm: 0 i: 22, pairs changed

fullset, iterNUm: 0 i: 259, pairs changed 42
fullset, iterNUm: 0 i: 260, pairs changed 42
fullset, iterNUm: 0 i: 261, pairs changed 42
fullset, iterNUm: 0 i: 262, pairs changed 42
fullset, iterNUm: 0 i: 263, pairs changed 42
fullset, iterNUm: 0 i: 264, pairs changed 42
fullset, iterNUm: 0 i: 265, pairs changed 42
fullset, iterNUm: 0 i: 266, pairs changed 42
fullset, iterNUm: 0 i: 267, pairs changed 42
fullset, iterNUm: 0 i: 268, pairs changed 42
fullset, iterNUm: 0 i: 269, pairs changed 42
L==H
fullset, iterNUm: 0 i: 270, pairs changed 42
fullset, iterNUm: 0 i: 271, pairs changed 42
fullset, iterNUm: 0 i: 272, pairs changed 42
fullset, iterNUm: 0 i: 273, pairs changed 42
L==H
fullset, iterNUm: 0 i: 274, pairs changed 42
fullset, iterNUm: 0 i: 275, pairs changed 42
L==H
fullset, iterNUm: 0 i: 276, pairs changed 42
fullset, iterNUm: 0 i: 277, pairs changed 42
fullset, iterNUm: 0 i: 278, pairs changed 42
fullset, iterNUm: 0 i: 279, pairs changed 42
fullset, iterNUm: 0 i: 280, pairs change

L==H
fullset, iterNUm: 0 i: 448, pairs changed 42
L==H
fullset, iterNUm: 0 i: 449, pairs changed 42
L==H
fullset, iterNUm: 0 i: 450, pairs changed 42
L==H
fullset, iterNUm: 0 i: 451, pairs changed 42
L==H
fullset, iterNUm: 0 i: 452, pairs changed 42
L==H
fullset, iterNUm: 0 i: 453, pairs changed 42
L==H
fullset, iterNUm: 0 i: 454, pairs changed 42
L==H
fullset, iterNUm: 0 i: 455, pairs changed 42
L==H
fullset, iterNUm: 0 i: 456, pairs changed 42
L==H
fullset, iterNUm: 0 i: 457, pairs changed 42
L==H
fullset, iterNUm: 0 i: 458, pairs changed 42
L==H
fullset, iterNUm: 0 i: 459, pairs changed 42
L==H
fullset, iterNUm: 0 i: 460, pairs changed 42
L==H
fullset, iterNUm: 0 i: 461, pairs changed 42
L==H
fullset, iterNUm: 0 i: 462, pairs changed 42
fullset, iterNUm: 0 i: 463, pairs changed 42
L==H
fullset, iterNUm: 0 i: 464, pairs changed 42
L==H
fullset, iterNUm: 0 i: 465, pairs changed 42
L==H
fullset, iterNUm: 0 i: 466, pairs changed 42
L==H
fullset, iterNUm: 0 i: 467, pairs changed 42
L==H


L==H
fullset, iterNUm: 0 i: 625, pairs changed 42
L==H
fullset, iterNUm: 0 i: 626, pairs changed 42
L==H
fullset, iterNUm: 0 i: 627, pairs changed 42
L==H
fullset, iterNUm: 0 i: 628, pairs changed 42
L==H
fullset, iterNUm: 0 i: 629, pairs changed 42
L==H
fullset, iterNUm: 0 i: 630, pairs changed 42
L==H
fullset, iterNUm: 0 i: 631, pairs changed 42
L==H
fullset, iterNUm: 0 i: 632, pairs changed 42
L==H
fullset, iterNUm: 0 i: 633, pairs changed 42
L==H
fullset, iterNUm: 0 i: 634, pairs changed 42
L==H
fullset, iterNUm: 0 i: 635, pairs changed 42
L==H
fullset, iterNUm: 0 i: 636, pairs changed 42
L==H
fullset, iterNUm: 0 i: 637, pairs changed 42
L==H
fullset, iterNUm: 0 i: 638, pairs changed 42
L==H
fullset, iterNUm: 0 i: 639, pairs changed 42
L==H
fullset, iterNUm: 0 i: 640, pairs changed 42
L==H
fullset, iterNUm: 0 i: 641, pairs changed 42
L==H
fullset, iterNUm: 0 i: 642, pairs changed 42
L==H
fullset, iterNUm: 0 i: 643, pairs changed 42
L==H
fullset, iterNUm: 0 i: 644, pairs changed 42


L==H
fullset, iterNUm: 0 i: 794, pairs changed 42
L==H
fullset, iterNUm: 0 i: 795, pairs changed 42
L==H
fullset, iterNUm: 0 i: 796, pairs changed 42
fullset, iterNUm: 0 i: 797, pairs changed 42
L==H
fullset, iterNUm: 0 i: 798, pairs changed 42
L==H
fullset, iterNUm: 0 i: 799, pairs changed 42
L==H
fullset, iterNUm: 0 i: 800, pairs changed 42
L==H
fullset, iterNUm: 0 i: 801, pairs changed 42
L==H
fullset, iterNUm: 0 i: 802, pairs changed 42
L==H
fullset, iterNUm: 0 i: 803, pairs changed 42
L==H
fullset, iterNUm: 0 i: 804, pairs changed 42
L==H
fullset, iterNUm: 0 i: 805, pairs changed 42
L==H
fullset, iterNUm: 0 i: 806, pairs changed 42
L==H
fullset, iterNUm: 0 i: 807, pairs changed 42
L==H
fullset, iterNUm: 0 i: 808, pairs changed 42
L==H
fullset, iterNUm: 0 i: 809, pairs changed 42
L==H
fullset, iterNUm: 0 i: 810, pairs changed 42
L==H
fullset, iterNUm: 0 i: 811, pairs changed 42
L==H
fullset, iterNUm: 0 i: 812, pairs changed 42
L==H
fullset, iterNUm: 0 i: 813, pairs changed 42
L==H


...

j not moving enough
fullset, iterNUm: 8 i: 1061, pairs changed 0
fullset, iterNUm: 8 i: 1062, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1063, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1064, pairs changed 0
fullset, iterNUm: 8 i: 1065, pairs changed 0
fullset, iterNUm: 8 i: 1066, pairs changed 0
fullset, iterNUm: 8 i: 1067, pairs changed 0
fullset, iterNUm: 8 i: 1068, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1069, pairs changed 0
fullset, iterNUm: 8 i: 1070, pairs changed 0
fullset, iterNUm: 8 i: 1071, pairs changed 0
fullset, iterNUm: 8 i: 1072, pairs changed 0
fullset, iterNUm: 8 i: 1073, pairs changed 0
fullset, iterNUm: 8 i: 1074, pairs changed 0
fullset, iterNUm: 8 i: 1075, pairs changed 0
fullset, iterNUm: 8 i: 1076, pairs changed 0
fullset, iterNUm: 8 i: 1077, pairs changed 0
fullset, iterNUm: 8 i: 1078, pairs changed 0
fullset, iterNUm: 8 i: 1079, pairs changed 0
fullset, iterNUm: 8 i: 1080, pairs changed 0
fullset, iterNUm: 8 i: 1081, pairs changed 0
fullset, iterNUm: 8 

j not moving enough
fullset, iterNUm: 8 i: 1358, pairs changed 0
fullset, iterNUm: 8 i: 1359, pairs changed 0
fullset, iterNUm: 8 i: 1360, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1361, pairs changed 0
fullset, iterNUm: 8 i: 1362, pairs changed 0
fullset, iterNUm: 8 i: 1363, pairs changed 0
fullset, iterNUm: 8 i: 1364, pairs changed 0
fullset, iterNUm: 8 i: 1365, pairs changed 0
fullset, iterNUm: 8 i: 1366, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1367, pairs changed 0
fullset, iterNUm: 8 i: 1368, pairs changed 0
fullset, iterNUm: 8 i: 1369, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1370, pairs changed 0
fullset, iterNUm: 8 i: 1371, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1372, pairs changed 0
fullset, iterNUm: 8 i: 1373, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1374, pairs changed 0
fullset, iterNUm: 8 i: 1375, pairs changed 0
fullset, iterNUm: 8 i: 1376, pairs changed 0
fullset, iterNUm: 8 i: 1377, pairs changed 0
fullset, iterNUm: 8 i: 13

j not moving enough
fullset, iterNUm: 8 i: 1540, pairs changed 0
fullset, iterNUm: 8 i: 1541, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1542, pairs changed 0
fullset, iterNUm: 8 i: 1543, pairs changed 0
fullset, iterNUm: 8 i: 1544, pairs changed 0
fullset, iterNUm: 8 i: 1545, pairs changed 0
fullset, iterNUm: 8 i: 1546, pairs changed 0
fullset, iterNUm: 8 i: 1547, pairs changed 0
fullset, iterNUm: 8 i: 1548, pairs changed 0
fullset, iterNUm: 8 i: 1549, pairs changed 0
fullset, iterNUm: 8 i: 1550, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1551, pairs changed 0
fullset, iterNUm: 8 i: 1552, pairs changed 0
fullset, iterNUm: 8 i: 1553, pairs changed 0
fullset, iterNUm: 8 i: 1554, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1555, pairs changed 0
fullset, iterNUm: 8 i: 1556, pairs changed 0
fullset, iterNUm: 8 i: 1557, pairs changed 0
fullset, iterNUm: 8 i: 1558, pairs changed 0
fullset, iterNUm: 8 i: 1559, pairs changed 0
fullset, iterNUm: 8 i: 1560, pairs changed 0
fulls

fullset, iterNUm: 8 i: 1716, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1717, pairs changed 0
fullset, iterNUm: 8 i: 1718, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1719, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1720, pairs changed 0
fullset, iterNUm: 8 i: 1721, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1722, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1723, pairs changed 0
fullset, iterNUm: 8 i: 1724, pairs changed 0
fullset, iterNUm: 8 i: 1725, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1726, pairs changed 0
fullset, iterNUm: 8 i: 1727, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1728, pairs changed 0
L==H
fullset, iterNUm: 8 i: 1729, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1730, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1731, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1732, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1733, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1734, pairs changed 0
j not

j not moving enough
fullset, iterNUm: 8 i: 1855, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1856, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1857, pairs changed 0
fullset, iterNUm: 8 i: 1858, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1859, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1860, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1861, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1862, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1863, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1864, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1865, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1866, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1867, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1868, pairs changed 0
j not moving enough
fullset, iterNUm: 8 i: 1869, pairs changed 0
fullset, iterNUm: 8 i: 1870, pairs changed 0
